In [1]:
import requests
import pandas as pd
import pycountry_convert as pc
import json

In [2]:
url_prefix = "http://www.numbeo.com:8008/"
from API_Key import api_key as api_key

### Cities

In [3]:
# API URL
url_api = f"/api/cities?api_key={api_key}"
url_1 = url_prefix + url_api

# API request
response_1 = requests.get(url_1)
output_1 = response_1.json()
print(output_1)

{'cities': [{'country': 'Algeria', 'city': 'Abelessa', 'latitude': 22.1877766, 'city_id': 1, 'longitude': 4.0695454}, {'country': 'Algeria', 'city': 'Adrar', 'latitude': 27.8756137, 'city_id': 2, 'longitude': -0.2907496}, {'country': 'Algeria', 'city': 'Aflu', 'latitude': 34.113883, 'city_id': 3, 'longitude': 2.097262}, {'country': 'Algeria', 'city': 'Algiers', 'latitude': 36.752887, 'city_id': 4, 'longitude': 3.042048}, {'country': 'Algeria', 'city': 'Annaba', 'latitude': 36.902859, 'city_id': 5, 'longitude': 7.755543}, {'country': 'Algeria', 'city': 'Batna', 'latitude': 35.552991, 'city_id': 6, 'longitude': 6.1775324}, {'country': 'Algeria', 'city': 'Bechar', 'latitude': 31.6160969, 'city_id': 7, 'longitude': -2.2166234}, {'country': 'Algeria', 'city': 'Bejaia', 'latitude': 36.75, 'city_id': 8, 'longitude': 5.0666667}, {'country': 'Algeria', 'city': 'Biskra', 'latitude': 34.8507647, 'city_id': 9, 'longitude': 5.7280575}, {'country': 'Algeria', 'city': 'Blida', 'latitude': 36.480499, 

In [4]:
output_1.keys()

dict_keys(['cities'])

In [5]:
cities = pd.read_csv('cities_raw.csv')

In [33]:
cities = pd.DataFrame(output_1['cities'])
cities

country      city   latitude  city_id  longitude
0          Algeria  Abelessa  22.187777        1   4.069545
1          Algeria     Adrar  27.875614        2  -0.290750
2          Algeria      Aflu  34.113883        3   2.097262
3          Algeria   Algiers  36.752887        4   3.042048
4          Algeria    Annaba  36.902859        5   7.755543
...            ...       ...        ...      ...        ...
17616  Switzerland  Brissago  46.120044    14163   8.711266
17617  Switzerland   Muralto  46.172962    14164   8.805608
17618  Switzerland     Cevio  46.317706    14166   8.602308
17619   Costa Rica    Atenas   9.978494    14167 -84.373839
17620        India      Moga  30.816460    14168  75.171709

[17621 rows x 5 columns]

In [6]:
cities.to_csv('cities_raw.csv', index=False)

In [6]:
def country_to_continent(country_name):
    country_alpha2 = pc.country_name_to_country_alpha2(country_name)
    country_continent_code = pc.country_alpha2_to_continent_code(country_alpha2)
    country_continent_name = pc.convert_continent_code_to_continent_name(country_continent_code)
    return country_continent_name

In [7]:
# testing
country_name = 'Italy'
print(country_to_continent(country_name))
country_name = 'Chile'
print(country_to_continent(country_name))

Europe
South America


In [8]:
continents = []
for country in cities['country']:
    try:
        continent_name = country_to_continent(country)
        continents.append(continent_name)
    except:
        continents.append('none')

In [9]:
continents_df = pd.DataFrame(continents)
continents_df.columns = ['continent']
continents_df

continent
0             Africa
1             Africa
2             Africa
3             Africa
4             Africa
...              ...
17619         Europe
17620         Europe
17621         Europe
17622  North America
17623           Asia

[17624 rows x 1 columns]

In [10]:
continents_df.value_counts()

continent    
Europe           4921
North America    4224
Asia             3597
Africa           2557
South America    1321
Oceania           664
none              340
dtype: int64

In [11]:
cities_2 = pd.concat([cities,continents_df],axis=1)
cities_2

country      city   latitude  city_id  longitude      continent
0          Algeria  Abelessa  22.187777        1   4.069545         Africa
1          Algeria     Adrar  27.875614        2  -0.290750         Africa
2          Algeria      Aflu  34.113883        3   2.097262         Africa
3          Algeria   Algiers  36.752887        4   3.042048         Africa
4          Algeria    Annaba  36.902859        5   7.755543         Africa
...            ...       ...        ...      ...        ...            ...
17619  Switzerland  Brissago  46.120044    14163   8.711266         Europe
17620  Switzerland   Muralto  46.172962    14164   8.805608         Europe
17621  Switzerland     Cevio  46.317706    14166   8.602308         Europe
17622   Costa Rica    Atenas   9.978494    14167 -84.373839  North America
17623        India      Moga  30.816460    14168  75.171709           Asia

[17624 rows x 6 columns]

In [12]:
nones_continents = list(cities_2[cities_2['continent']=='none']['country'].unique())
nones_continents

['French Southern Territories',
 'Bosnia And Herzegovina',
 'Sint Maarten',
 'Reunion',
 'Wallis And Futuna',
 'Saint Helena',
 'Saint Vincent And The Grenadines',
 'Tristan Da Cunha',
 'Western Sahara',
 'Antigua And Barbuda',
 'Trinidad And Tobago',
 'Isle Of Man',
 'Kosovo (Disputed Territory)',
 'Curacao',
 'Pitcairn',
 'Saint Kitts And Nevis',
 'Saint-Pierre And Miquelon',
 'South Georgia And The South Sandwich Islands',
 'Turks And Caicos Islands',
 'Us Virgin Islands',
 'Hong Kong (China)',
 'Macao (China)',
 'Sao Tome And Principe',
 'Timor-Leste',
 'Aland Islands',
 'Alderney',
 'Svalbard And Jan Mayen',
 'Vatican City']

In [13]:
cont_mapping = {
    'French Southern Territories': 'Antarctica',
    'Bosnia And Herzegovina': 'Europe',
    'Sint Maarten': 'North America',
    'Reunion': 'Africa',
    'Wallis And Futuna': 'Oceania',
    'Saint Helena': 'Africa',
    'Saint Vincent And The Grenadines': 'North America',
    'Tristan Da Cunha': 'Africa',
    'Western Sahara': 'Africa',
    'Antigua And Barbuda': 'North America',
    'Trinidad And Tobago': 'North America',
    'Isle Of Man': 'Europe',
    'Kosovo (Disputed Territory)': 'Europe',
    'Curacao': 'North America',
    'Pitcairn': 'Oceania',
    'Saint Kitts And Nevis': 'North America',
    'Saint-Pierre And Miquelon': 'North America',
    'South Georgia And The South Sandwich Islands': 'Antarctica',
    'Turks And Caicos Islands': 'North America',
    'Us Virgin Islands': 'North America',
    'Hong Kong (China)': 'Asia',
    'Macao (China)': 'Asia',
    'Sao Tome And Principe': 'Africa',
    'Timor-Leste': 'Asia',
    'Aland Islands': 'Europe',
    'Alderney': 'Europe',
    'Svalbard And Jan Mayen': 'Europe',
    'Vatican City': 'Europe'
}

In [14]:
for index, row in cities_2.iterrows():
    if row['continent'] == 'none':
        country = row['country']
        if country in cont_mapping:
            cities_2.at[index, 'continent'] = cont_mapping[country]

In [15]:
# cities_2['continent'] = cities_2.apply(lambda row: cont_mapping[row['country']] if row['continent'] == 'none' and row['country'] in cont_mapping else row['continent'], axis=1)

In [18]:
cities_2['continent'].value_counts()

Europe           5033
North America    4363
Asia             3612
Africa           2610
South America    1321
Oceania           682
Antarctica          3
Name: continent, dtype: int64

In [17]:
cities_2

country      city   latitude  city_id  longitude      continent
0          Algeria  Abelessa  22.187777        1   4.069545         Africa
1          Algeria     Adrar  27.875614        2  -0.290750         Africa
2          Algeria      Aflu  34.113883        3   2.097262         Africa
3          Algeria   Algiers  36.752887        4   3.042048         Africa
4          Algeria    Annaba  36.902859        5   7.755543         Africa
...            ...       ...        ...      ...        ...            ...
17619  Switzerland  Brissago  46.120044    14163   8.711266         Europe
17620  Switzerland   Muralto  46.172962    14164   8.805608         Europe
17621  Switzerland     Cevio  46.317706    14166   8.602308         Europe
17622   Costa Rica    Atenas   9.978494    14167 -84.373839  North America
17623        India      Moga  30.816460    14168  75.171709           Asia

[17624 rows x 6 columns]

In [22]:
cities_2.to_csv('cities_countries_continents.csv', index=False)

### Currency Exchange Rates

In [19]:
# API URL
url_api = f"/api/currency_exchange_rates?api_key={api_key}"
url_2 = url_prefix + url_api

# API request
response_2 = requests.get(url_2)
output_2 = response_2.json()
print(output_2)

{'exchange_rates': [{'one_usd_to_currency': 3.673025, 'currency': 'AED', 'one_eur_to_currency': 4.009633753616069}, {'one_usd_to_currency': 87.499985, 'currency': 'AFN', 'one_eur_to_currency': 95.51878718410568}, {'one_usd_to_currency': 97.875, 'currency': 'ALL', 'one_eur_to_currency': 106.84460455215327}, {'one_usd_to_currency': 386.06, 'currency': 'AMD', 'one_eur_to_currency': 421.4398777359315}, {'one_usd_to_currency': 1.802442, 'currency': 'ANG', 'one_eur_to_currency': 1.967624037989193}, {'one_usd_to_currency': 825.4999999999999, 'currency': 'AOA', 'one_eur_to_currency': 901.1516838600513}, {'one_usd_to_currency': 1.5008499999999998, 'currency': 'AUD', 'one_eur_to_currency': 1.6383931008132744}, {'one_usd_to_currency': 1.8025, 'currency': 'AWG', 'one_eur_to_currency': 1.967687353310409}, {'one_usd_to_currency': 1.7053829999999999, 'currency': 'AZN', 'one_eur_to_currency': 1.8616702145079418}, {'one_usd_to_currency': 1.798826, 'currency': 'BAM', 'one_eur_to_currency': 1.96367665520

In [20]:
output_2.keys()

dict_keys(['exchange_rates', 'last_update'])

In [21]:
currency = pd.DataFrame(output_2['exchange_rates'])
currency

one_usd_to_currency currency  one_eur_to_currency
0               3.673025      AED             4.009634
1              87.499985      AFN            95.518787
2              97.875000      ALL           106.844605
3             386.060000      AMD           421.439878
4               1.802442      ANG             1.967624
..                   ...      ...                  ...
154           109.313842      XPF           119.331742
155           250.349961      YER           273.292900
156            18.820355      ZAR            20.545118
157            17.513670      ZMW            19.118683
158           322.000000      ZWL           351.509197

[159 rows x 3 columns]

In [22]:
currency[currency['currency']=='GBP']

one_usd_to_currency currency  one_eur_to_currency
45             0.786999      GBP             0.859122

In [27]:
currency.to_csv('currency.csv', index=False)

### Price Items

In [23]:
# API URL
url_api = f"/api/price_items?api_key={api_key}"
url_3 = url_prefix + url_api

# API request
response_3 = requests.get(url_3)
output_3 = response_3.json()
print(output_3)

{'items': [{'rent_factor': 0, 'cpi_factor': 16, 'item_id': 1, 'name': 'Meal, Inexpensive Restaurant', 'category': 'Restaurants'}, {'rent_factor': 0, 'cpi_factor': 3.5, 'item_id': 2, 'name': 'Meal for 2 People, Mid-range Restaurant, Three-course', 'category': 'Restaurants'}, {'rent_factor': 0, 'cpi_factor': 6, 'item_id': 3, 'name': 'McMeal at McDonalds (or Equivalent Combo Meal)', 'category': 'Restaurants'}, {'rent_factor': 0, 'cpi_factor': 5, 'item_id': 4, 'name': 'Domestic Beer (0.5 liter draught)', 'category': 'Restaurants'}, {'rent_factor': 0, 'cpi_factor': 5, 'item_id': 5, 'name': 'Imported Beer (0.33 liter bottle)', 'category': 'Restaurants'}, {'rent_factor': 0, 'cpi_factor': 6, 'item_id': 6, 'name': 'Coke/Pepsi (0.33 liter bottle)', 'category': 'Restaurants'}, {'rent_factor': 0, 'cpi_factor': 6, 'item_id': 7, 'name': 'Water (0.33 liter bottle) ', 'category': 'Restaurants'}, {'rent_factor': 0, 'cpi_factor': 25, 'item_id': 8, 'name': 'Milk (regular), (1 liter)', 'category': 'Market

In [24]:
output_3.keys()

dict_keys(['items'])

In [25]:
price_items = pd.DataFrame(output_3['items'])
price_items

rent_factor  cpi_factor  item_id  \
0          0.00     16.0000        1   
1          0.00      3.5000        2   
2          0.00      6.0000        3   
3          0.00      5.0000        4   
4          0.00      5.0000        5   
5          0.00      6.0000        6   
6          0.00      6.0000        7   
7          0.00     25.0000        8   
8          0.00     31.0000        9   
9          0.00     20.0000       11   
10         0.00     12.0000       12   
11         0.00     30.0000       13   
12         0.00      4.0000       14   
13         0.00      6.0000       15   
14         0.00      6.0000       16   
15         0.00     15.0000       17   
16         0.00     20.0000       18   
17         0.00      1.5000       20   
18         0.00     31.0000      110   
19         0.25      0.0000       26   
20         0.25      0.0000       27   
21         0.25      0.0000       28   
22         0.25      0.0000       29   
23         0.00      1.0000       30   
24         0.00      1.0000       33   
25         0.00      0.0000      100   
26         0.00      0.0000      101   
27         0.00      0.0000      105   
28         0.00      0.0000      106   
29         0.00     60.0000       24   
30         0.00      2.3000       40   
31         0.00      3.0000       42   
32         0.00      6.0000       44   
33         0.00     15.0000       19   
34         0.00      0.0035       25   
35         0.00      0.3500       60   
36         0.00      0.3500       62   
37         0.00      0.3500       64   
38         0.00      0.3500       66   
39         0.00      5.0000      107   
40         0.00     20.0000      108   
41         0.00      0.7000      109   
42         0.00     30.0000      111   
43         0.00     24.0000      112   
44         0.00     18.0000      113   
45         0.00     15.0000      114   
46         0.00     14.0000      115   
47         0.00     22.0000      116   
48         0.00     25.0000      118   
49         0.00     10.0000      119   
50         0.00     15.0000      121   
51         0.00      0.0035      206   
52         0.00      0.0000      224   
53         0.00      0.0000      228   
54         0.00      4.0000       34   

                                                 name                category  
0                        Meal, Inexpensive Restaurant             Restaurants  
1   Meal for 2 People, Mid-range Restaurant, Three...             Restaurants  
2      McMeal at McDonalds (or Equivalent Combo Meal)             Restaurants  
3                   Domestic Beer (0.5 liter draught)             Restaurants  
4                   Imported Beer (0.33 liter bottle)             Restaurants  
5                      Coke/Pepsi (0.33 liter bottle)             Restaurants  
6                          Water (0.33 liter bottle)              Restaurants  
7                           Milk (regular), (1 liter)                 Markets  
8                    Loaf of Fresh White Bread (500g)                 Markets  
9                                 Eggs (regular) (12)                 Markets  
10                                 Local Cheese (1kg)                 Markets  
11                           Water (1.5 liter bottle)                 Markets  
12                         Bottle of Wine (Mid-Range)                 Markets  
13                   Domestic Beer (0.5 liter bottle)                 Markets  
14                  Imported Beer (0.33 liter bottle)                 Markets  
15                      Cigarettes 20 Pack (Marlboro)                 Markets  
16                   One-way Ticket (Local Transport)          Transportation  
17                       Monthly Pass (Regular Price)          Transportation  
18                                       Apples (1kg)                 Markets  
19               Apartment (1 bedroom) in City Centre          Rent Per Month  
20            Apartment (1 bedroom) Outside of Centre          Rent Per Month  
21 

In [31]:
price_items.to_csv('price_items.csv', index=False)

### Historical city prices

In [26]:
# API URL
url_api = f"api/historical_city_prices?api_key={api_key}&query=London,%20United%20Kingdom"
url_4 = url_prefix + url_api

# API request
response_4 = requests.get(url_4)
output_4 = response_4.json()
print(output_4)

{'entry': [{'amount': 10.4, 'year': 2010, 'item_id': 1}, {'amount': 13.971830985915494, 'year': 2011, 'item_id': 1}, {'amount': 10, 'year': 2012, 'item_id': 1}, {'amount': 10, 'year': 2013, 'item_id': 1}, {'amount': 10, 'year': 2014, 'item_id': 1}, {'amount': 14, 'year': 2015, 'item_id': 1}, {'amount': 15, 'year': 2016, 'item_id': 1}, {'amount': 15, 'year': 2017, 'item_id': 1}, {'amount': 15, 'year': 2018, 'item_id': 1}, {'amount': 15, 'year': 2019, 'item_id': 1}, {'amount': 15, 'year': 2020, 'item_id': 1}, {'amount': 15, 'year': 2021, 'item_id': 1}, {'amount': 16.5, 'year': 2022, 'item_id': 1}, {'amount': 47.5, 'year': 2010, 'item_id': 2}, {'amount': 50, 'year': 2011, 'item_id': 2}, {'amount': 50, 'year': 2012, 'item_id': 2}, {'amount': 50, 'year': 2013, 'item_id': 2}, {'amount': 50, 'year': 2014, 'item_id': 2}, {'amount': 50, 'year': 2015, 'item_id': 2}, {'amount': 55, 'year': 2016, 'item_id': 2}, {'amount': 54.835, 'year': 2017, 'item_id': 2}, {'amount': 50, 'year': 2018, 'item_id':

In [27]:
output_4.keys()

dict_keys(['entry', 'city', 'currency'])

In [28]:
output_4['city']

'London, United Kingdom'

In [29]:
historicals = pd.DataFrame(output_4['entry'])
historicals['city_country'] = output_4['city']
historicals['currency'] = output_4['currency']
historicals

amount  year  item_id            city_country currency
0       10.400000  2010        1  London, United Kingdom      GBP
1       13.971831  2011        1  London, United Kingdom      GBP
2       10.000000  2012        1  London, United Kingdom      GBP
3       10.000000  2013        1  London, United Kingdom      GBP
4       10.000000  2014        1  London, United Kingdom      GBP
..            ...   ...      ...                     ...      ...
648  16752.823529  2018      228  London, United Kingdom      GBP
649  18342.857143  2019      228  London, United Kingdom      GBP
650  18333.333333  2020      228  London, United Kingdom      GBP
651  17361.538462  2021      228  London, United Kingdom      GBP
652  18425.000000  2022      228  London, United Kingdom      GBP

[653 rows x 5 columns]

In [32]:
historicals[historicals['item_id']==26]

amount  year  item_id            city_country currency
246  1125.000000  2010       26  London, United Kingdom      GBP
247  1438.571429  2011       26  London, United Kingdom      GBP
248  1401.111111  2012       26  London, United Kingdom      GBP
249  1526.346349  2013       26  London, United Kingdom      GBP
250  1530.485957  2014       26  London, United Kingdom      GBP
251  1673.875048  2015       26  London, United Kingdom      GBP
252  1677.223684  2016       26  London, United Kingdom      GBP
253  1657.553767  2017       26  London, United Kingdom      GBP
254  1683.575187  2018       26  London, United Kingdom      GBP
255  1760.073333  2019       26  London, United Kingdom      GBP
256  1730.996404  2020       26  London, United Kingdom      GBP
257  1711.846154  2021       26  London, United Kingdom      GBP
258  1873.179941  2022       26  London, United Kingdom      GBP

In [38]:
output_4['currency']

'GBP'

In [33]:
europe_cities = list(cities_2[cities_2['continent']=='Europe']['city'])
europe_countries = list(cities_2[cities_2['continent']=='Europe']['country'])

In [34]:
europe_cities

['Mondim de Basto',
 'Avallon',
 'Lousã',
 'Valverde de El Hierro',
 'Botevgrad',
 'Sittensen',
 'Gouda',
 'Bathgate',
 'Zory (Źory)',
 'Eyemouth',
 'Crewe',
 'Albergaria-A-Velha',
 'Saverne',
 'Alençon',
 'Göppingen',
 'Miroslava',
 'Notodden',
 'Wittenberg',
 'Alta',
 'Wielun (Wieluń)',
 'Syros',
 'Tarifa',
 'Grays',
 'Jena',
 'Hellerup',
 'Winhöring',
 'Rushden',
 'Ust-Labinsk',
 'Bromölla',
 'Settle',
 'Belebey',
 'Orestiada',
 'Melun',
 'Svetlahorsk',
 'Albox',
 'Špindlerův Mlýn',
 'Izegem',
 'Syzran',
 'Uberherrn (Überherrn)',
 'Stupino',
 'Boston',
 'Żywiec (Zywiec)',
 'Elverum',
 'Saariselka',
 'Pomezia',
 'Oban',
 'Tuzi',
 'Svetogorsk',
 'Brisighella',
 'Vik i Myrdal',
 'Evry',
 'Foix',
 'Snezhnogorsk',
 'Grigaiciai',
 'Banbury',
 'Široki Brijeg',
 'Hengelo',
 'Redditch, Worcestershire',
 'Chrudim',
 'Val Thorens',
 'Yllas (Yllästunturi)',
 'Yuzhne',
 'Kettering',
 'Pevek',
 'Kyzyl',
 'Budaörs (Budaors)',
 'Backnang',
 'Ustroń',
 'Gretna',
 'Annan',
 'Kutná Hora (Kutna Hora)',

In [35]:
eu_cities_dict = {}
for city in europe_cities:
    eu_cities_dict[city] = europe_countries[europe_cities.index(city)]

eu_cities_dict = dict(sorted(eu_cities_dict.items()))
eu_cities_dict

{"'s-Gravenzande": 'Netherlands',
 "'s-Hertogenbosch": 'Netherlands',
 'Aabenraa': 'Denmark',
 'Aachen': 'Germany',
 'Aalborg': 'Denmark',
 'Aalen': 'Germany',
 'Aalst': 'Belgium',
 'Aanekoski': 'Finland',
 'Aarau': 'Switzerland',
 'Aarschot': 'Belgium',
 'Abakan': 'Russia',
 'Abano Terme': 'Italy',
 'Abaza': 'Russia',
 'Abensberg': 'Germany',
 'Aberdare': 'United Kingdom',
 'Aberdeen': 'United Kingdom',
 'Abersoch': 'United Kingdom',
 'Aberystwyth': 'United Kingdom',
 'Abingdon-on-Thames': 'United Kingdom',
 'Abrantes': 'Portugal',
 'Accrington': 'United Kingdom',
 'Acharnes (Axarnai)': 'Greece',
 'Acheres': 'France',
 'Achill Island': 'Ireland',
 'Achisnk': 'Russia',
 'Acqualagna PU': 'Italy',
 'Acquapendente': 'Italy',
 'Acquarossa': 'Switzerland',
 'Acquaviva': 'San Marino',
 'Adra': 'Spain',
 'Aegiali': 'Greece',
 'Aegina': 'Greece',
 'Affoltern am Albis': 'Switzerland',
 'Agapa': 'Russia',
 'Agen': 'France',
 'Aginskoye': 'Russia',
 'Agioi Theodoroi (Korinth)': 'Greece',
 'Agios 

In [36]:
europe_cities_sorted = sorted(europe_cities)
europe_countries_sorted = sorted(europe_countries)

In [37]:
len(europe_cities_sorted)

5033

In [38]:
europe_cities_sorted.index('Tampa')

4207

In [39]:
pd.Series(europe_countries_sorted).unique()

array(['Aland Islands', 'Albania', 'Alderney', 'Andorra', 'Austria',
       'Belarus', 'Belgium', 'Bosnia And Herzegovina', 'Bulgaria',
       'Croatia', 'Czech Republic', 'Denmark', 'Estonia', 'Faroe Islands',
       'Finland', 'France', 'Germany', 'Gibraltar', 'Greece', 'Guernsey',
       'Hungary', 'Iceland', 'Ireland', 'Isle Of Man', 'Italy', 'Jersey',
       'Kosovo (Disputed Territory)', 'Latvia', 'Liechtenstein',
       'Lithuania', 'Luxembourg', 'Malta', 'Moldova', 'Monaco',
       'Montenegro', 'Netherlands', 'North Macedonia', 'Norway', 'Poland',
       'Portugal', 'Romania', 'Russia', 'San Marino', 'Serbia',
       'Slovakia', 'Slovenia', 'Spain', 'Svalbard And Jan Mayen',
       'Sweden', 'Switzerland', 'Ukraine', 'United Kingdom',
       'Vatican City'], dtype=object)

In [40]:
europe_countries_adj = []
for country in europe_countries:
    europe_countries_adj.append(country.replace(' ','%20'))

In [41]:
europe_cities_sorted.index('London')

2420

In [48]:
# Getting historical prices for european cities
hist_cities = pd.DataFrame()
for i in range(len(europe_cities)):
    url_api = f"api/historical_city_prices?api_key={api_key}&query={europe_cities[i]},{europe_countries_adj[i]}"
    url_temp = url_prefix + url_api

    response_temp = requests.get(url_temp)
    output_temp = response_temp.json()
    
    temp_df = pd.DataFrame()
    
    try:
        temp_df = pd.DataFrame(output_temp['entry'])
        temp_df['city_country'] = output_temp['city']
        temp_df['currency'] = output_temp['currency']
        
        hist_cities = pd.concat([hist_cities,temp_df],axis=0)

    except:
        None
    
hist_cities

amount  year  item_id       city_country currency
0   12.900000  2020        1  Best, Netherlands      EUR
1   12.250000  2021        1  Best, Netherlands      EUR
2   52.000000  2020        2  Best, Netherlands      EUR
3   49.000000  2021        2  Best, Netherlands      EUR
4    8.000000  2020        3  Best, Netherlands      EUR
..        ...   ...      ...                ...      ...
29   4.747500  2021      111    Rzeszow, Poland      PLN
30   5.800000  2017      114    Rzeszow, Poland      PLN
31   8.000000  2020      114    Rzeszow, Poland      PLN
32   8.434467  2022      114    Rzeszow, Poland      PLN
33   5.750000  2022      118    Rzeszow, Poland      PLN

[88182 rows x 5 columns]

In [60]:
hist_cities.to_csv('hist_cities_europe_raw.csv', index=False)

In [124]:
#hist_cities = pd.read_csv('hist_cities_europe_raw.csv')

In [125]:
hist_cities = hist_cities.sort_values(['city_country','item_id','year']).reset_index(drop=True)
hist_cities

amount  year  item_id         city_country currency
0         10.000000  2014        1      Aachen, Germany      EUR
1          9.500000  2016        1      Aachen, Germany      EUR
2          9.000000  2017        1      Aachen, Germany      EUR
3          9.000000  2018        1      Aachen, Germany      EUR
4          8.000000  2019        1      Aachen, Germany      EUR
...             ...   ...      ...                  ...      ...
88177  27100.000000  2018      228  Zurich, Switzerland      CHF
88178  33794.756667  2019      228  Zurich, Switzerland      CHF
88179  29500.000000  2020      228  Zurich, Switzerland      CHF
88180  30466.666667  2021      228  Zurich, Switzerland      CHF
88181  29200.000000  2022      228  Zurich, Switzerland      CHF

[88182 rows x 5 columns]

In [126]:
len(list(hist_cities['city_country'].unique()))

320

In [127]:
hist_cities[hist_cities['city_country']=='Tampa, FL, United States']

amount  year  item_id              city_country currency
74482     12.500000  2010        1  Tampa, FL, United States      USD
74483      8.250000  2011        1  Tampa, FL, United States      USD
74484     10.000000  2012        1  Tampa, FL, United States      USD
74485     12.000000  2013        1  Tampa, FL, United States      USD
74486     10.000000  2014        1  Tampa, FL, United States      USD
...             ...   ...      ...                       ...      ...
74996    853.333333  2017      224  Tampa, FL, United States      USD
74997    933.222222  2019      224  Tampa, FL, United States      USD
74998    685.833333  2020      224  Tampa, FL, United States      USD
74999   1125.000000  2022      224  Tampa, FL, United States      USD
75000  21250.000000  2021      228  Tampa, FL, United States      USD

[519 rows x 5 columns]

In [128]:
cities_2[(cities_2['city']=="Tampa") | (cities_2['city'] == "Tampa, FL")]

country       city   latitude  city_id  longitude      continent
5234   United States  Tampa, FL  27.947522     3492 -82.458428  North America
13417         France      Tampa  47.902423     8437   6.621414         Europe

In [129]:
# France and United Stats both have a city named 'Tampa'. When requesting historical prices for Tampa, France the API retrives
# the city in the United States as French Tampa does not have info available. So Tampa will be removed.
hist_cities_2 = hist_cities.drop(hist_cities[hist_cities['city_country'] == 'Tampa, FL, United States'].index)

In [130]:
hist_cities_2[hist_cities_2['city_country']=='Tampa, FL, United States']

Empty DataFrame
Columns: [amount, year, item_id, city_country, currency]
Index: []

In [131]:
len(list(hist_cities_2['city_country'].unique()))

319

In [132]:
country_name = 'Russia'
print(country_to_continent(country_name))

Europe


In [133]:
hist_cities_country_split = hist_cities_2['city_country'].str.split(', ', expand=True)
hist_cities_country_split.columns = ['city','country']
hist_cities_country_split

city      country
0      Aachen      Germany
1      Aachen      Germany
2      Aachen      Germany
3      Aachen      Germany
4      Aachen      Germany
...       ...          ...
88177  Zurich  Switzerland
88178  Zurich  Switzerland
88179  Zurich  Switzerland
88180  Zurich  Switzerland
88181  Zurich  Switzerland

[87663 rows x 2 columns]

In [134]:
sorted(list(hist_cities_country_split['country'].unique()))

['Albania',
 'Austria',
 'Belarus',
 'Belgium',
 'Bosnia And Herzegovina',
 'Bulgaria',
 'Croatia',
 'Czech Republic',
 'Denmark',
 'Estonia',
 'Finland',
 'France',
 'Germany',
 'Greece',
 'Hungary',
 'Iceland',
 'Ireland',
 'Isle Of Man',
 'Italy',
 'Jersey',
 'Kosovo (Disputed Territory)',
 'Latvia',
 'Lithuania',
 'Luxembourg',
 'Malta',
 'Moldova',
 'Montenegro',
 'Netherlands',
 'North Macedonia',
 'Norway',
 'Poland',
 'Portugal',
 'Romania',
 'Russia',
 'Serbia',
 'Slovakia',
 'Slovenia',
 'Spain',
 'Sweden',
 'Switzerland',
 'Ukraine',
 'United Kingdom']

In [135]:
hist_cities_2 = pd.concat([hist_cities_2,hist_cities_country_split], axis=1)
hist_cities_2 = hist_cities_2.drop(columns=['city_country'])
hist_cities_2

amount  year  item_id currency    city      country
0         10.000000  2014        1      EUR  Aachen      Germany
1          9.500000  2016        1      EUR  Aachen      Germany
2          9.000000  2017        1      EUR  Aachen      Germany
3          9.000000  2018        1      EUR  Aachen      Germany
4          8.000000  2019        1      EUR  Aachen      Germany
...             ...   ...      ...      ...     ...          ...
88177  27100.000000  2018      228      CHF  Zurich  Switzerland
88178  33794.756667  2019      228      CHF  Zurich  Switzerland
88179  29500.000000  2020      228      CHF  Zurich  Switzerland
88180  30466.666667  2021      228      CHF  Zurich  Switzerland
88181  29200.000000  2022      228      CHF  Zurich  Switzerland

[87663 rows x 6 columns]

In [136]:
russian_cities = hist_cities_2[hist_cities_2['country']=='Russia']['city'].unique()
russian_cities

array(['Barnaul', 'Chelyabinsk', 'Irkutsk', 'Izhevsk', 'Kaliningrad',
       'Kazan', 'Kemerovo', 'Khabarovsk', 'Krasnodar', 'Krasnoyarsk',
       'Moscow', 'Nizhny Novgorod', 'Novosibirsk', 'Omsk', 'Perm',
       'Rostov-na-donu', 'Saint Petersburg', 'Samara', 'Saratov',
       'Simferopol', 'Sochi', 'Tolyatti (Togliatti)', 'Tomsk', 'Tyumen',
       'Ufa', 'Vladivostok', 'Volgograd', 'Voronezh', 'Yaroslavl',
       'Yekaterinburg'], dtype=object)

In [137]:
russian_cities_continent = {
    'Barnaul': 'Asia',
    'Chelyabinsk': 'Asia',
    'Irkutsk': 'Asia',
    'Izhevsk': 'Europe',
    'Kaliningrad': 'Europe',
    'Kazan': 'Europe',
    'Kemerovo': 'Asia',
    'Khabarovsk': 'Asia',
    'Krasnodar': 'Europe',
    'Krasnoyarsk': 'Asia',
    'Moscow': 'Europe',
    'Nizhny Novgorod': 'Europe',
    'Novosibirsk': 'Asia',
    'Omsk': 'Asia',
    'Perm': 'Europe',
    'Rostov-na-donu': 'Europe',
    'Saint Petersburg': 'Europe',
    'Samara': 'Europe',
    'Saratov': 'Europe',
    'Simferopol': 'Europe',
    'Sochi': 'Europe',
    'Tolyatti (Togliatti)': 'Europe',
    'Tomsk': 'Asia',
    'Tyumen': 'Asia',
    'Ufa': 'Asia',
    'Vladivostok': 'Asia',
    'Volgograd': 'Europe',
    'Voronezh': 'Europe',
    'Yaroslavl': 'Europe',
    'Yekaterinburg': 'Asia'
}

In [138]:
russia_asia_cities = [city for city, continent in russian_cities_continent.items() if continent == 'Asia']
hist_cities_3 = hist_cities_2[~hist_cities_2['city'].isin(russia_asia_cities)]
hist_cities_3

amount  year  item_id currency    city      country
0         10.000000  2014        1      EUR  Aachen      Germany
1          9.500000  2016        1      EUR  Aachen      Germany
2          9.000000  2017        1      EUR  Aachen      Germany
3          9.000000  2018        1      EUR  Aachen      Germany
4          8.000000  2019        1      EUR  Aachen      Germany
...             ...   ...      ...      ...     ...          ...
88177  27100.000000  2018      228      CHF  Zurich  Switzerland
88178  33794.756667  2019      228      CHF  Zurich  Switzerland
88179  29500.000000  2020      228      CHF  Zurich  Switzerland
88180  30466.666667  2021      228      CHF  Zurich  Switzerland
88181  29200.000000  2022      228      CHF  Zurich  Switzerland

[85431 rows x 6 columns]

In [139]:
print(len(list(russian_cities))-len(russia_asia_cities))
print(len(list(hist_cities_3[hist_cities_3['country']=='Russia']['city'].unique())))

17
17


In [140]:
len(list(russian_cities))

30

In [141]:
hist_cities_4 = hist_cities_3.drop_duplicates()
hist_cities_4

amount  year  item_id currency    city      country
0         10.000000  2014        1      EUR  Aachen      Germany
1          9.500000  2016        1      EUR  Aachen      Germany
2          9.000000  2017        1      EUR  Aachen      Germany
3          9.000000  2018        1      EUR  Aachen      Germany
4          8.000000  2019        1      EUR  Aachen      Germany
...             ...   ...      ...      ...     ...          ...
88177  27100.000000  2018      228      CHF  Zurich  Switzerland
88178  33794.756667  2019      228      CHF  Zurich  Switzerland
88179  29500.000000  2020      228      CHF  Zurich  Switzerland
88180  30466.666667  2021      228      CHF  Zurich  Switzerland
88181  29200.000000  2022      228      CHF  Zurich  Switzerland

[77797 rows x 6 columns]

In [142]:
hist_cities_country_split_2_unique = hist_cities_4[['city','country']].drop_duplicates()
hist_cities_country_split_2_unique

city         country
0                    Aachen         Germany
222                 Aalborg         Denmark
414                Aberdeen  United Kingdom
756                Alicante           Spain
1025                 Almere     Netherlands
...                     ...             ...
86680                Zagreb         Croatia
87334          Zaporizhzhya         Ukraine
87416  Zaragoza (Saragossa)           Spain
87485                   Zug     Switzerland
87541                Zurich     Switzerland

[306 rows x 2 columns]

In [143]:
hist_cities_country_split_2_unique['country'].value_counts()

United Kingdom                 40
Germany                        27
Italy                          25
Netherlands                    18
Russia                         17
Spain                          15
Poland                         14
France                         13
Romania                        13
Ukraine                        11
Portugal                        8
Greece                          7
Croatia                         7
Switzerland                     7
Norway                          6
Austria                         6
Czech Republic                  6
Ireland                         5
Serbia                          5
Belgium                         5
Sweden                          5
Finland                         5
Bulgaria                        4
Hungary                         4
Bosnia And Herzegovina          4
Denmark                         4
Slovakia                        3
Lithuania                       3
Slovenia                        2
Estonia       

In [139]:
#hist_cities_2.to_csv('historical_prices_europe_cities_ADJ.csv', index=False)

In [145]:
hist_cities_5 = hist_cities_4.merge(price_items, on='item_id', how='left')
hist_cities_5 = hist_cities_5.merge(currency[['currency','one_eur_to_currency']], on='currency', how='left')
hist_cities_5

amount  year  item_id currency    city      country  rent_factor  \
0         10.000000  2014        1      EUR  Aachen      Germany          0.0   
1          9.500000  2016        1      EUR  Aachen      Germany          0.0   
2          9.000000  2017        1      EUR  Aachen      Germany          0.0   
3          9.000000  2018        1      EUR  Aachen      Germany          0.0   
4          8.000000  2019        1      EUR  Aachen      Germany          0.0   
...             ...   ...      ...      ...     ...          ...          ...   
77792  27100.000000  2018      228      CHF  Zurich  Switzerland          0.0   
77793  33794.756667  2019      228      CHF  Zurich  Switzerland          0.0   
77794  29500.000000  2020      228      CHF  Zurich  Switzerland          0.0   
77795  30466.666667  2021      228      CHF  Zurich  Switzerland          0.0   
77796  29200.000000  2022      228      CHF  Zurich  Switzerland          0.0   

       cpi_factor                                              name  \
0            16.0                      Meal, Inexpensive Restaurant   
1            16.0                      Meal, Inexpensive Restaurant   
2            16.0                      Meal, Inexpensive Restaurant   
3            16.0                      Meal, Inexpensive Restaurant   
4            16.0                      Meal, Inexpensive Restaurant   
...           ...                                               ...   
77792         0.0  International Primary School, Yearly for 1 Child   
77793         0.0  International Primary School, Yearly for 1 Child   
77794         0.0  International Primary School, Yearly for 1 Child   
77795         0.0  International Primary School, Yearly for 1 Child   
77796         0.0  International Primary School, Yearly for 1 Child   

          category  one_eur_to_currency  
0      Restaurants             1.000000  
1      Restaurants             1.000000  
2      Restaurants             1.000000  
3      Restaurants             1.000000  
4      Restaurants             1.000000  
...            ...                  ...  
77792    Childcare             0.976736  
77793    Childcare             0.976736  
77794    Childcare             0.976736  
77795    Childcare             0.976736  
77796    Childcare             0.976736  

[77797 rows x 11 columns]

In [146]:
hist_cities_5['currency'].unique()

array(['EUR', 'DKK', 'GBP', 'RON', 'BAM', 'CHF', 'RSD', 'NOK', 'PLN',
       'MKD', 'BYN', 'CZK', 'HUF', 'BGN', 'MDL', 'UAH', 'SEK', 'RUB',
       'ISK', 'ALL'], dtype=object)

In [147]:
len(list(hist_cities_5['currency'].unique()))

20

In [149]:
hist_cities_5.to_csv('historical_prices_europe_cities_clean.csv', index=False)

### Indices

In [3]:
# API URL
url_api = f"api/indices?api_key={api_key}&query=London,%20United%20Kingdom"
url_5 = url_prefix + url_api

# API request
response_5 = requests.get(url_5)
output_5 = response_5.json()
print(output_5)

{'crime_index': 53.907934579390535, 'cpi_and_rent_index': 76.53787790442401, 'purchasing_power_incl_rent_index': 83.02065702418707, 'property_price_to_income_ratio': 16.685937384130533, 'contributors_healthcare': 372, 'safety_index': 46.092065420609465, 'traffic_co2_index': 1998.6839826839828, 'traffic_inefficiency_index': 197.67246911107486, 'contributors_traffic': 248, 'rent_index': 69.6204161925801, 'health_care_index': 69.74759141704256, 'groceries_index': 58.93591568996456, 'contributors_property': 95, 'pollution_index': 57.73925840805185, 'traffic_time_index': 45.96536796536797, 'restaurant_price_index': 96.21412870146406, 'contributors_cost_of_living': 625, 'climate_index': 88.25433798690545, 'cpi_index': 82.82451916700208, 'quality_of_life_index': 127.12753252688243, 'contributors_pollution': 386, 'contributors_crime': 1157, 'traffic_index': 167.63090438417424, 'name': 'London, United Kingdom', 'city_id': 6512}


In [23]:
output_5.keys()

dict_keys(['crime_index', 'cpi_and_rent_index', 'purchasing_power_incl_rent_index', 'property_price_to_income_ratio', 'contributors_healthcare', 'safety_index', 'traffic_co2_index', 'traffic_inefficiency_index', 'contributors_traffic', 'rent_index', 'health_care_index', 'groceries_index', 'contributors_property', 'pollution_index', 'traffic_time_index', 'restaurant_price_index', 'contributors_cost_of_living', 'climate_index', 'cpi_index', 'quality_of_life_index', 'contributors_pollution', 'contributors_crime', 'traffic_index', 'name', 'city_id'])

In [24]:
output_5

{'crime_index': 53.892247904118705,
 'cpi_and_rent_index': 76.68739713630389,
 'purchasing_power_incl_rent_index': 81.17412508397312,
 'property_price_to_income_ratio': 16.157041543705674,
 'contributors_healthcare': 372,
 'safety_index': 46.1077520958813,
 'traffic_co2_index': 1998.6839826839828,
 'traffic_inefficiency_index': 197.67246911107486,
 'contributors_traffic': 248,
 'rent_index': 70.1319006125079,
 'health_care_index': 69.74759141704256,
 'groceries_index': 59.52722642216942,
 'contributors_property': 92,
 'pollution_index': 57.73925840805185,
 'traffic_time_index': 45.96536796536797,
 'restaurant_price_index': 96.09006842436966,
 'contributors_cost_of_living': 648,
 'climate_index': 88.25433798690545,
 'cpi_index': 82.61060363179593,
 'quality_of_life_index': 126.94705048237823,
 'contributors_pollution': 386,
 'contributors_crime': 1155,
 'traffic_index': 167.63090438417424,
 'name': 'London, United Kingdom',
 'city_id': 6512}

In [31]:
pd.DataFrame(output_5,index=[0]).T

0
crime_index                                    53.892248
cpi_and_rent_index                             76.687397
purchasing_power_incl_rent_index               81.174125
property_price_to_income_ratio                 16.157042
contributors_healthcare                              372
safety_index                                   46.107752
traffic_co2_index                            1998.683983
traffic_inefficiency_index                    197.672469
contributors_traffic                                 248
rent_index                                     70.131901
health_care_index                              69.747591
groceries_index                                59.527226
contributors_property                                 92
pollution_index                                57.739258
traffic_time_index                             45.965368
restaurant_price_index                         96.090068
contributors_cost_of_living                          648
climate_index                                  88.254338
cpi_index                                      82.610604
quality_of_life_index                          126.94705
contributors_pollution                               386
contributors_crime                                  1155
traffic_index                                 167.630904
name                              London, United Kingdom
city_id                                             6512

### Historical Indices

In [3]:
# API URL
url_api = f"api/rankings_by_city_historical?api_key={api_key}&section=4"
url_5 = url_prefix + url_api

# API request
response_5 = requests.get(url_5)
output_5 = response_5.json()
output_5 = dict(sorted(output_5.items()))
print(output_5)

{'2012-Q1': [{'country': 'India', 'city_name': 'Kolkata', 'time_exp_index': 39925.0564498103, 'traffic_index': 355.422756576394, 'time_index': 74.25, 'inefficiency_index': 579.995661426699, 'co2_emission_index': 19684.000000000022, 'city_id': 4032}, {'country': 'Iran', 'city_name': 'Tehran', 'time_exp_index': 38296.1800864727, 'traffic_index': 328.173074159631, 'time_index': 73.5, 'inefficiency_index': 351.26919273469, 'co2_emission_index': 9714, 'city_id': 6749}, {'country': 'Turkey', 'city_name': 'Istanbul', 'time_exp_index': 40255.9964477414, 'traffic_index': 308.117534843034, 'time_index': 74.4, 'inefficiency_index': 239.961471118564, 'co2_emission_index': 1855.9999999999977, 'city_id': 6404}, {'country': 'India', 'city_name': 'Pune', 'time_exp_index': 23220.4827638701, 'traffic_index': 291.196265838767, 'time_index': 65.3333333333333, 'inefficiency_index': 444.682642169589, 'co2_emission_index': 16470, 'city_id': 4049}, {'country': 'United Kingdom', 'city_name': 'London', 'time_ex

In [126]:
output_5.keys()

dict_keys(['2012-Q1', '2013-Q1', '2014', '2014-mid', '2015', '2015-mid', '2016', '2016-mid', '2017', '2017-mid', '2018', '2018-mid', '2019', '2019-mid', '2020', '2020-mid', '2021', '2021-mid', '2022', '2022-mid', '2023', '2023-mid'])

In [21]:
list(output_5.keys())

['2009',
 '2010',
 '2011',
 '2012',
 '2013',
 '2014',
 '2014-mid',
 '2015',
 '2015-mid',
 '2016',
 '2016-mid',
 '2017',
 '2017-mid',
 '2018',
 '2018-mid',
 '2019',
 '2019-mid',
 '2020',
 '2020-mid',
 '2021',
 '2021-mid',
 '2022',
 '2022-mid',
 '2023',
 '2023-mid']

In [5]:
hist_indices = {'cost_of_living': 1, 'property_prices': 2, 'traffic': 4, 'crime': 7, 'pollution': 8, 'quality_of_life': 12}
indexes = list(hist_indices.keys())

i = 0
for key in hist_indices.keys():
    # API URL
    url_api = f"api/rankings_by_city_historical?api_key={api_key}&section={hist_indices[key]}"
    url_temp = url_prefix + url_api

    # API request
    response_temp = requests.get(url_temp)
    output_temp = response_temp.json()
    output_temp = dict(sorted(output_temp.items()))

    # Column names
    columns = ['year'] + list(pd.DataFrame(output_temp[list(output_temp.keys())[0]]).columns)
    indexes[i] = pd.DataFrame(columns=columns)

    # Joining yearly dataframes
    for key in output_temp.keys():
        temp_df = pd.DataFrame()
        temp_df['year'] = [key] * len(output_temp[key])
        temp_df[pd.DataFrame(output_temp[key]).columns] = pd.DataFrame(output_temp[key])
        indexes[i] = pd.concat([indexes[i],temp_df])
    
    i += 1


In [6]:
cost_of_living = indexes[0]
property_prices = indexes[1]
traffic = indexes[2]
crime = indexes[3]
pollution = indexes[4]
quality_of_life = indexes[5]

In [11]:
cost_of_living.to_csv('cost_of_living.csv', index=False)
property_prices.to_csv('property_prices.csv', index=False)
traffic.to_csv('traffic.csv', index=False)
crime.to_csv('crime.csv', index=False)
pollution.to_csv('pollution.csv', index=False)
quality_of_life.to_csv('quality_of_life.csv', index=False)

In [21]:
# Saving JSON file
file_path = 'indices_test.json'

with open(file_path, 'w') as file:
    json.dump(output_5, file)

print("JSON file saved successfully.")

JSON file saved successfully.


In [23]:
# Loading JSON file
file_path = 'indices_test.json'

with open(file_path, 'r') as file:
    output_5 = json.load(file)

print(output_5)

{'2020-mid': [{'country': 'Switzerland', 'city_name': 'Zurich', 'cpi_and_rent_index': 98.80333355150216, 'rent_index': 64.36890115529944, 'purchasing_power_incl_rent_index': 121.11735429720454, 'restaurant_price_index': 120.38647500609562, 'groceries_index': 131.22978274257514, 'city_id': 6379, 'cpi_index': 131.4883943334502}, {'country': 'Switzerland', 'city_name': 'Lugano', 'cpi_and_rent_index': 86.65717230521128, 'rent_index': 40.204932141752856, 'purchasing_power_incl_rent_index': 101.15475315934373, 'restaurant_price_index': 115.18645996739482, 'groceries_index': 134.799149220362, 'city_id': 6362, 'cpi_index': 130.74950046473447}, {'country': 'Switzerland', 'city_name': 'Basel', 'cpi_and_rent_index': 89.72312954761954, 'rent_index': 46.60616873381468, 'purchasing_power_incl_rent_index': 109.89984198471193, 'restaurant_price_index': 131.92276406170222, 'groceries_index': 126.04580461792969, 'city_id': 6348, 'cpi_index': 130.64962047149766}, {'country': 'Switzerland', 'city_name': '

In [10]:
section1 = pd.DataFrame(output_5['2022'])
section1

country        city_name  time_exp_index  traffic_index  \
0    United States  Los Angeles, CA    17151.718449     344.057779   
1          Nigeria            Lagos    25546.004915     340.377983   
2       Costa Rica         San Jose    21222.464465     331.118807   
3        Sri Lanka          Colombo    18612.441530     307.663927   
4            India            Delhi    12791.743591     285.090608   
..             ...              ...             ...            ...   
241        Romania           Brasov       20.000000      76.464122   
242         Serbia         Novi Sad       16.363636      72.680283   
243    Switzerland            Basel       20.793103      70.511221   
244        Croatia            Split       16.866667      66.808998   
245    Netherlands             Best       15.520000      37.096770   

     time_index  inefficiency_index  co2_emission_index  city_id  
0     61.069892          790.168310        15354.526882     3442  
1     66.777778          473.312427         8466.444444     1407  
2     64.017241          361.890906        10485.517241     7384  
3     62.173913          422.117601         7835.275362     4740  
4     57.369565          315.473131         9381.644269     4016  
..          ...                 ...                 ...      ...  
241   20.000000           40.179165         2084.222222     6047  
242   16.363636           77.724346         1888.363636     6205  
243   20.793103           46.039329         1472.482759     6348  
244   16.866667           85.383969         1339.200000     7484  
245   15.520000           12.716209          198.000000    36281  

[246 rows x 8 columns]

In [25]:
section1[['country','city_name']].sort_values(['country','city_name']).reset_index(drop=True)

country         city_name
0    Afghanistan             Kabul
1        Albania            Tirana
2        Algeria           Algiers
3      Argentina      Buenos Aires
4        Armenia           Yerevan
..           ...               ...
573    Venezuela           Caracas
574      Vietnam             Hanoi
575      Vietnam  Ho Chi Minh City
576       Zambia            Lusaka
577     Zimbabwe            Harare

[578 rows x 2 columns]

In [26]:
hist_cities_5 = pd.read_csv('historical_prices_europe_cities_clean.csv')
hist_cities_5

amount  year  item_id currency    city      country  rent_factor  \
0         10.000000  2014        1      EUR  Aachen      Germany          0.0   
1          9.500000  2016        1      EUR  Aachen      Germany          0.0   
2          9.000000  2017        1      EUR  Aachen      Germany          0.0   
3          9.000000  2018        1      EUR  Aachen      Germany          0.0   
4          8.000000  2019        1      EUR  Aachen      Germany          0.0   
...             ...   ...      ...      ...     ...          ...          ...   
77792  27100.000000  2018      228      CHF  Zurich  Switzerland          0.0   
77793  33794.756667  2019      228      CHF  Zurich  Switzerland          0.0   
77794  29500.000000  2020      228      CHF  Zurich  Switzerland          0.0   
77795  30466.666667  2021      228      CHF  Zurich  Switzerland          0.0   
77796  29200.000000  2022      228      CHF  Zurich  Switzerland          0.0   

       cpi_factor                                              name  \
0            16.0                      Meal, Inexpensive Restaurant   
1            16.0                      Meal, Inexpensive Restaurant   
2            16.0                      Meal, Inexpensive Restaurant   
3            16.0                      Meal, Inexpensive Restaurant   
4            16.0                      Meal, Inexpensive Restaurant   
...           ...                                               ...   
77792         0.0  International Primary School, Yearly for 1 Child   
77793         0.0  International Primary School, Yearly for 1 Child   
77794         0.0  International Primary School, Yearly for 1 Child   
77795         0.0  International Primary School, Yearly for 1 Child   
77796         0.0  International Primary School, Yearly for 1 Child   

          category  one_eur_to_currency  
0      Restaurants             1.000000  
1      Restaurants             1.000000  
2      Restaurants             1.000000  
3      Restaurants             1.000000  
4      Restaurants             1.000000  
...            ...                  ...  
77792    Childcare             0.976736  
77793    Childcare             0.976736  
77794    Childcare             0.976736  
77795    Childcare             0.976736  
77796    Childcare             0.976736  

[77797 rows x 11 columns]

In [27]:
EU_cities = hist_cities_5[['city','country']].drop_duplicates()
EU_cities

city         country
0                    Aachen         Germany
222                 Aalborg         Denmark
414                Aberdeen  United Kingdom
756                Alicante           Spain
1025                 Almere     Netherlands
...                     ...             ...
76295                Zagreb         Croatia
76949          Zaporizhzhya         Ukraine
77031  Zaragoza (Saragossa)           Spain
77100                   Zug     Switzerland
77156                Zurich     Switzerland

[306 rows x 2 columns]

In [28]:
section1[section1['city_name'].isin(EU_cities['city'])]

country city_name  cpi_and_rent_index  rent_index  \
1                    Switzerland    Zurich          102.187674   69.264642   
2                    Switzerland     Basel           92.699863   49.377910   
3                    Switzerland       Zug          101.872655   72.116661   
4                    Switzerland    Lugano           86.958447   44.994841   
5                    Switzerland  Lausanne           92.743364   59.554089   
..                           ...       ...                 ...         ...   
498                      Moldova  Chisinau           21.783993   10.411488   
506                      Ukraine   Kharkiv           21.618914   11.603814   
513                      Ukraine      Lviv           20.701299   10.534887   
516                      Ukraine    Dnipro           20.462082   10.486601   
535  Kosovo (Disputed Territory)  Pristina           18.131799    9.042651   

     purchasing_power_incl_rent_index  restaurant_price_index  \
1                          129.792429              132.520769   
2                          111.530749              130.949791   
3                          143.395144              130.926074   
4                          111.963092              119.800391   
5                          127.008374              127.012347   
..                                ...                     ...   
498                         34.381277               26.560947   
506                         33.979374               24.610398   
513                         38.295686               24.347987   
516                         32.736594               23.655159   
535                         47.475068               19.694286   

     groceries_index  city_id   cpi_index  
1         136.140395     6379  131.238266  
2         137.070934     6348  130.926244  
3         132.607624     6378  128.128719  
4         129.173209     6362  123.986251  
5         122.562903     6360  122.028882  
..               ...      ...         ...  
498        25.523408     5895   31.818853  
506        26.137632     6435   30.456028  
513        26.617737     8179   29.671928  
516        24.569073     7394   29.264238  
535        22.985593     8436   26.151872  

[230 rows x 9 columns]

In [45]:
pd.DataFrame(output_5[list(output_5.keys())[0]]).columns

Index(['country', 'city_name', 'cpi_and_rent_index', 'rent_index',
       'purchasing_power_incl_rent_index', 'restaurant_price_index',
       'groceries_index', 'city_id', 'cpi_index'],
      dtype='object')

In [82]:
columns = ['year'] + list(pd.DataFrame(output_5[list(output_5.keys())[0]]).columns)
sec1_df = pd.DataFrame(columns=columns)
sec1_df.columns

Index(['year', 'country', 'city_name', 'cpi_and_rent_index', 'rent_index',
       'purchasing_power_incl_rent_index', 'restaurant_price_index',
       'groceries_index', 'city_id', 'cpi_index'],
      dtype='object')

In [83]:
for key in output_5.keys():
    temp_df = pd.DataFrame()
    temp_df['year'] = [key] * len(output_5[key])
    temp_df[pd.DataFrame(output_5[key]).columns] = pd.DataFrame(output_5[key])
    sec1_df = pd.concat([sec1_df,temp_df])
sec1_df

year   country   city_name  cpi_and_rent_index  rent_index  \
0        2009    France       Paris          115.352399   96.391765   
1        2009   Ireland      Dublin          111.119488   87.581765   
2        2009   Belgium    Brussels          102.157894   78.771765   
3        2009   Germany      Berlin           82.605699   32.959765   
4        2009    Sweden   Stockholm           79.754064   29.987690   
..        ...       ...         ...                 ...         ...   
544  2023-mid     Egypt        Giza           11.997886    2.826395   
545  2023-mid     Egypt  Alexandria           11.843187    3.104335   
546  2023-mid  Pakistan      Lahore           11.843707    3.323732   
547  2023-mid  Pakistan   Islamabad           11.759416    4.529720   
548  2023-mid  Pakistan     Karachi           10.919585    2.921131   

     purchasing_power_incl_rent_index  restaurant_price_index  \
0                           39.378386              116.526933   
1                           59.250192              131.562667   
2                           55.583183              107.555612   
3                           58.581072               79.188196   
4                           63.872003               85.248661   
..                                ...                     ...   
544                         20.604704               14.427118   
545                         17.294788               17.057120   
546                         23.992232               16.368617   
547                         24.712172               13.895604   
548                         20.439475               12.740084   

     groceries_index city_id   cpi_index  
0         117.046357    5426  127.819457  
1         154.514000    5601  126.596087  
2         110.881808    5111  117.534817  
3          90.266599    5439  115.249054  
4          98.953456    7382  112.476610  
..               ...     ...         ...  
544        17.394378    6685   20.333007  
545        18.623761    6654   19.785122  
546        15.558201    7051   19.586725  
547        15.279598    7043   18.329819  
548        15.953401    7048   18.188640  

[10886 rows x 10 columns]

In [84]:
sec1_df['year'].value_counts()

2021        598
2022        578
2021-mid    563
2023-mid    549
2023        540
2018        538
2018-mid    535
2015-mid    515
2020-mid    514
2022-mid    510
2017-mid    509
2016        496
2017        483
2014        473
2015        457
2014-mid    443
2020        440
2019        433
2019-mid    377
2016-mid    372
2013        340
2012        257
2011        210
2010        115
2009         41
Name: year, dtype: int64

### ---

In [13]:
# API URL
url_api = f"/api/rankings_by_country_historical?api_key={api_key}&section=1"
url_6 = url_prefix + url_api

# API request
response_6 = requests.get(url_6)
output_6 = response_6.json()
print(output_6)

{'2020-mid': [{'country': 'Bermuda', 'cpi_and_rent_index': 117.54379076938952, 'rent_index': 85.70044612206502, 'purchasing_power_incl_rent_index': 78.17337665832203, 'iso3166_country_code': 'BM', 'restaurant_price_index': 152.51662810884065, 'groceries_index': 146.6266336349428, 'cpi_index': 147.76939876904675}, {'country': 'Switzerland', 'cpi_and_rent_index': 89.4132595851513, 'rent_index': 51.195540288434, 'purchasing_power_incl_rent_index': 114.83037471498125, 'iso3166_country_code': 'CH', 'restaurant_price_index': 118.55462137333879, 'groceries_index': 124.9302500638261, 'cpi_index': 125.68940503712005}, {'country': 'Norway', 'cpi_and_rent_index': 65.54076879417735, 'rent_index': 32.613669826766255, 'purchasing_power_incl_rent_index': 83.39569266201569, 'iso3166_country_code': 'NO', 'restaurant_price_index': 96.81304320197691, 'groceries_index': 89.55006192941389, 'cpi_index': 96.7950731701}, {'country': 'Iceland', 'cpi_and_rent_index': 65.0394145400725, 'rent_index': 38.542927993

In [71]:
output_6.keys()

dict_keys(['2020-mid', '2012', '2011', '2010', '2016-mid', '2018-mid', '2009', '2015-mid', '2019-mid', '2023-mid', '2023', '2022', '2021', '2014-mid', '2020', '2019', '2018', '2017', '2016', '2015', '2014', '2022-mid', '2013', '2021-mid', '2017-mid'])

In [17]:
country_section1 = pd.DataFrame(output_6['2018'])
country_section1

country  cpi_and_rent_index  rent_index  \
0        Bermuda          123.574424  100.705465   
1    Switzerland           93.987158   53.839541   
2        Iceland           90.524604   54.634062   
3         Norway           78.568881   40.852629   
4        Bahamas           69.158600   35.314504   
..           ...                 ...         ...   
110      Tunisia           17.128784    5.812512   
111        India           17.177318    6.765295   
112      Ukraine           17.720700    8.852036   
113        Egypt           15.745378    5.074215   
114     Pakistan           15.537992    5.292625   

     purchasing_power_incl_rent_index iso3166_country_code  \
0                          104.239985                   BM   
1                          126.147027                   CH   
2                           87.843087                   IS   
3                          107.950072                   NO   
4                           71.400957                   BS   
..                                ...                  ...   
110                         38.225286                   TN   
111                         79.273169                   IN   
112                         30.239313                   UA   
113                         24.671694                   EG   
114                         41.114544                   PK   

     restaurant_price_index  groceries_index   cpi_index  
0                151.590351       143.416162  144.877146  
1                131.859719       133.339467  131.385165  
2                132.590999       118.952819  123.957092  
3                125.039210       106.517203  113.702042  
4                102.079477        88.382155  100.684799  
..                      ...              ...         ...  
110               17.051347        26.411211   27.670033  
111               18.336143        27.462993   26.876249  
112               18.618871        20.382603   25.981972  
113               21.024084        23.011214   25.685701  
114               19.024052        23.809710   25.081680  

[115 rows x 8 columns]

In [21]:
country_section1[country_section1['country']=='Montenegro']

country  cpi_and_rent_index  rent_index  \
73  Montenegro           28.224773   10.849288   

    purchasing_power_incl_rent_index iso3166_country_code  \
73                         48.683803                   ME   

    restaurant_price_index  groceries_index  cpi_index  
73               38.076847        35.753895  44.410254

In [3]:
hist_indices = {'cost_of_living': 1, 'property_prices': 2, 'traffic': 4, 'crime': 7, 'pollution': 8, 'quality_of_life': 12}
indexes_country = list(hist_indices.keys())

i = 0
for key in hist_indices.keys():
    # API URL
    url_api = f"api/rankings_by_country_historical?api_key={api_key}&section={hist_indices[key]}"
    url_temp = url_prefix + url_api

    # API request
    response_temp = requests.get(url_temp)
    output_temp = response_temp.json()
    output_temp = dict(sorted(output_temp.items()))

    # Column names
    columns = ['year'] + list(pd.DataFrame(output_temp[list(output_temp.keys())[0]]).columns)
    indexes_country[i] = pd.DataFrame(columns=columns)

    # Joining yearly dataframes
    for key in output_temp.keys():
        temp_df = pd.DataFrame()
        temp_df['year'] = [key] * len(output_temp[key])
        temp_df[pd.DataFrame(output_temp[key]).columns] = pd.DataFrame(output_temp[key])
        indexes_country[i] = pd.concat([indexes_country[i],temp_df])
    
    i += 1


In [4]:
cost_of_living_country = indexes_country[0]
property_prices_country = indexes_country[1]
traffic_country = indexes_country[2]
crime_country = indexes_country[3]
pollution_country = indexes_country[4]
quality_of_life_country = indexes_country[5]

In [5]:
cost_of_living_country.to_csv('cost_of_living_country.csv', index=False)
property_prices_country.to_csv('property_prices_country.csv', index=False)
traffic_country.to_csv('traffic_country.csv', index=False)
crime_country.to_csv('crime_country.csv', index=False)
pollution_country.to_csv('pollution_country.csv', index=False)
quality_of_life_country.to_csv('quality_of_life_country.csv', index=False)